In [1]:
# TODO: Remove irrelevant attributes
#   - Remove ones with high correlation with other attributes (confidence matrix, which only really works for numeric)
#   - Should not ignore high variance, because that could lead to overfitting, which we deal with by reducing variance
# TODO: Use oversampling (i.e. SMOTE) to resolve the class imbalance between the number of samples between the two classes
# TODO: Normalisation or standardisation

In [2]:
import pandas as pd
import numpy as np

In [3]:
data = pd.read_csv("data2021.student.csv", delimiter=',', header=[0])  # No attributes

print(data)

        ID  Class  C1   C2  C3    C4  C5  C6  C7  C8  ...  C23 C24 C25 C26  \
0        1    1.0  53  yes  V5  11.0  V2  V1  V1  V3  ...    1  V3  11  V2   
1        2    0.0  35  yes  V3  11.0  V7  V1  V1  V1  ...    2  V1  11  V4   
2        3    1.0  40  yes  V5  18.0  V2  V1  V2  V3  ...    1  V2  18  V3   
3        4    0.0  28  yes  V3  14.0  V7  V1  V1  V4  ...    1  V1  14  V2   
4        5    0.0  40  yes  V3  11.0  V1  V1  V4  V1  ...    1  V1  11  V3   
...    ...    ...  ..  ...  ..   ...  ..  ..  ..  ..  ...  ...  ..  ..  ..   
1095  1096    NaN  31  yes  V3  48.0  V3  V1  V1  V4  ...    1  V2  48  V2   
1096  1097    NaN  39  yes  V5  22.0  V3  V3  V4  V4  ...    1  V2  22  V2   
1097  1098    NaN  23  yes  V3  17.0  V2  V1  V1  V1  ...    2  V1  17  V4   
1098  1099    NaN  25   no  V2   5.0  V3  V1  V2  V1  ...    1  V2   5  V2   
1099  1100    NaN  34  yes  V3   7.0  V3  V1  V2  V1  ...    1  V2   7  V2   

     C27 C28  C29  C30   C31 C32  
0      4  V3  1.0    T  7865

In [4]:
# Class obviously should be categorical
data["Class"] = data["Class"].astype('category')

# Convert all attributes with data type 'object', representing non-numeric
# strings, to categorical
converting = []
for att in data:
    if data[att].dtype.name == 'object':
        data[att] = data[att].astype('category')
        converting.append(att)

print("Explicitly converted the following non-numeric attributes to categorical:")
print(converting, '\n')

Explicitly converted the following non-numeric attributes to categorical:
['C2', 'C3', 'C5', 'C6', 'C7', 'C8', 'C10', 'C11', 'C12', 'C13', 'C14', 'C18', 'C21', 'C22', 'C24', 'C26', 'C28', 'C30'] 



In [5]:
# TODO: Decide on which attributes to treat as numeric and which to treat as categorical
#   - Find numeric values which should actually be categorical

unique_threshold = 10
converting = []
for att in data:
    if data[att].dtype.name != 'category':
        if data[att].nunique() <= 10:
            data[att] = data[att].astype('category')
            converting.append(att)

print("Converted the following numeric attributes to categorical (due to few unique values):")
print(converting, '\n')

Converted the following numeric attributes to categorical (due to few unique values):
['C15', 'C17', 'C20', 'C23', 'C27', 'C29', 'C32'] 



In [6]:
# Drop the ID attribute, because it doesn't contribute anything to the classification; there is no point to including it
data.drop(['ID'], axis=1, inplace=True)
print("Dropped the ['ID'] attribute\n")

Dropped the ['ID'] attribute



In [7]:
# Remove all attributes with missing values more than the threshold
missing_threshold = 0.8
dropping = []
for att in data:
    missing = data[att].isnull().sum() / data[att].size
    if missing >= missing_threshold and att != 'Class':
        dropping.append(att)

print("Dropping the following attributes (due to too many missing values):")
print(dropping, '\n')
data.drop(dropping, axis=1, inplace=True)

Dropping the following attributes (due to too many missing values):
['C11', 'C32'] 



In [8]:
# Replace all numeric and nominal attributes with missing values less than the threshold with the global mean and mode respectively
impute_threshold = 0.05
imputed = []
for att in data:
    missing = data[att].isnull().sum() / data[att].size
    if missing < impute_threshold and missing != 0 and att != 'Class':
        # Replace values with the mode for nominal attributes
        if data[att].dtype.name == 'category':
            data[att].fillna(data[att].mode()[0], inplace=True)
        # Replace values with the mean for numeric attributes
        else:
            data[att].fillna(data[att].mean(), inplace=True)
        imputed.append(att)

print("Imputed mean (for numeric) and mode (for nominal) values for the following attributes (due to missing values):")
print(imputed)

Imputed mean (for numeric) and mode (for nominal) values for the following attributes (due to missing values):
['C3', 'C4', 'C13', 'C29']


In [9]:
# TODO: Data imputing for missing over impute_threshold?

In [10]:
# NOTE: Normalisation must be done before variance thresholding above 0.0

# Remove all attributes with extremely low variance below the threshold
var_threshold = 0.0 #TODO: Consider increasing this threshold; figure out if variance is dependent on scale
dropping = []
for att in data:
    if data[att].dtype.name != 'category':
        var = data[att].var()
        if var <= var_threshold and att != 'Class':
            dropping.append(att)

print("Dropping the following numeric attributes (due to extremely low variance):")
print(dropping, '\n')
data.drop(dropping, axis=1, inplace=True)

Dropping the following numeric attributes (due to extremely low variance):
[] 



In [11]:
# TODO: Check if there is a category with very few instances?

# This is done separately to the dropping attributes with low variance as in the case var_threshold > 0.0
dropping = []
for att in data:
    if data[att].dtype.name == 'category':
        if data[att].nunique() == 1:
            dropping.append(att)

print("Dropping the following categorical attributes (due to only having one unique value):")
print(dropping, '\n')
data.drop(dropping, axis=1, inplace=True)

Dropping the following categorical attributes (due to only having one unique value):
['C10', 'C15', 'C17', 'C30'] 



In [12]:
# Detect and delete all duplicate attributes, keeping the first found attribute
data_transposed = data.transpose()
data_transposed_is_duplicate = data_transposed.duplicated(subset=None, keep='first')
duplicate_cols_indices = np.where(data_transposed_is_duplicate == True)[0]
# Convert the tranpose 'row' indices, representing columns, to the relevant attribute names
duplicate_cols = data.columns[duplicate_cols_indices]

print("Dropping the following attributes (due to being duplicates):")
print(duplicate_cols, '\n')
data.drop(duplicate_cols, axis=1, inplace=True)

#TODO: Remove attributes where one attribute is a duplicate of the other, but with
#   a null value so that it's not detected

Dropping the following attributes (due to being duplicates):
Index(['C12', 'C26', 'C31'], dtype='object') 



In [13]:
# Detect and delete all duplicate instances, keeping the first found instance
data_is_duplicate = data.duplicated(subset=None, keep='first')
duplicate_rows = np.where(data_is_duplicate == True)[0]
data.drop(index=duplicate_rows, axis=0, inplace=True)

print("Dropping the following instances (due to being duplicates):")
print(duplicate_rows, '\n')

Dropping the following instances (due to being duplicates):
[900 901 902 903 904 905 906 907 908 909 910 911 912 913 914 915 916 917
 918 919 920 921 922 923 924 925 926 927 928 929 930 931 932 933 934 935
 936 937 938 939 940 941 942 943 944 945 946 947 948 949 950 951 952 953
 954 955 956 957 958 959 960 961 962 963 964 965 966 967 968 969 970 971
 972 973 974 975 976 977 978 979 980 981 982 983 984 985 986 987 988 989
 990 991 992 993 994 995 996 997 998 999] 



In [14]:
#TODO: Remove all instances that have only null values

In [15]:
print(data)

     Class  C1   C2  C3    C4  C5  C6  C7  C8    C9  ...   C19 C20  C21 C22  \
0      1.0  53  yes  V5  11.0  V2  V1  V1  V3  7865  ...  3824   4   V2  V2   
1      0.0  35  yes  V3  11.0  V7  V1  V1  V1  3904  ...  5160   2   V4  V1   
2      1.0  40  yes  V5  18.0  V2  V1  V2  V3  4296  ...  3720   3   V3  V2   
3      0.0  28  yes  V3  14.0  V7  V1  V1  V4  1402  ...  6245   4   V2  V1   
4      0.0  40  yes  V3  11.0  V1  V1  V4  V1  1503  ...  5496   4   V3  V1   
...    ...  ..  ...  ..   ...  ..  ..  ..  ..   ...  ...   ...  ..  ...  ..   
1095   NaN  31  yes  V3  48.0  V3  V1  V1  V4  6758  ...  4200   2   V2  V2   
1096   NaN  39  yes  V5  22.0  V3  V3  V4  V4  2674  ...  4844   4   V2  V1   
1097   NaN  23  yes  V3  17.0  V2  V1  V1  V1  2123  ...  4044   4   V4  V1   
1098   NaN  25   no  V2   5.0  V3  V1  V2  V1   589  ...  5054   3   V2  V1   
1099   NaN  34  yes  V3   7.0  V3  V1  V2  V1  2576  ...  5034   2   V2  V1   

      C23 C24 C25 C27 C28  C29  
0       1  V3  11 

In [16]:
data.describe()

C1           C4            C9            C16         C19  \
count  1000.00000  1000.000000   1000.000000    1000.000000  1000.00000   
mean     35.03900    20.464434   3270.739000   40647.645000  4999.92900   
std      11.39857    12.062116   2822.732086   28281.592319  1011.98354   
min      18.00000     3.000000    249.000000    1446.000000  2272.00000   
25%      26.00000    11.000000   1365.500000   19447.750000  4322.75000   
50%      32.00000    18.000000   2319.000000   33797.000000  4976.50000   
75%      41.00000    24.000000   3971.250000   56198.750000  5699.50000   
max      75.00000    72.000000  18424.000000  220716.000000  8633.00000   

               C25  
count  1000.000000  
mean     20.421000  
std      12.092559  
min       3.000000  
25%      11.000000  
50%      18.000000  
75%      24.000000  
max      72.000000

In [17]:
## TODO: TEMP
data.to_csv('output_pre_impute_over_threshold.csv')

In [18]:
import pandas_profiling ## TODO: TEMP
prof = pandas_profiling.ProfileReport(data)
prof.to_file(output_file='profile_DELETE_pre_impute_over_threshold.html')
data.profile_report()

Render HTML: 100%|██████████| 1/1 [00:02<00:00,  2.27s/it]
